In [1]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
from googletrans import Translator
import spacy
import en_core_web_sm
from collections import Counter
from spacy import displacy 
import locationtagger
from geopy.geocoders import Nominatim
from functools import partial
from geopy.extra.rate_limiter import RateLimiter
import numpy
import sqlite3
from selenium import webdriver
from selenium.webdriver.common.by import By
import time
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import datetime

In [16]:
def Set_up_WebScraping(url):
    
    driver = webdriver.Chrome(r"C:\Users\JourneyQ\OneDrive - kmutnb.ac.th\Desktop\Quick_file\year_2-S_2\Project_sofedev_2\Schap\chromedriver.exe")
    driver.get(url)

    for i in range(45):
        driver.execute_script("scrollBy(0,+500);")
        time.sleep(1)
    
    return driver.page_source

def YahooUpdateNews(share):

    url = requests.get(f"https://finance.yahoo.com/quote/{share}")
    chest,tag_share_news  = [],{}
    soup = BeautifulSoup(url.text, 'html')

    for div_all in soup.find_all('div', {'id': 'quoteNewsStream-0-Stream'}):

        for li in div_all.find_all('li', {'class': 'js-stream-content Pos(r)'}):

            for l in li.find_all('div', {'class': 'Py(14px) Pos(r)'}):

                df,st,share_tag  = {},'',{}
                
                tag_a = l.find('a')
                
                # Img
                tag_img = l.find('img')
                if str(tag_img) != 'None': url_img = l.find('img')['src']
                else : url_img = 'https://www.lifewire.com/thmb/yx5oJUJ4fA1TQ0h0pl9FM7Kc4Fo=/1500x0/filters:no_upscale():max_bytes(150000):strip_icc()/yahoo-logo-2019-879b7bed612d4bbc97065dce2a0f2d73.png'

                # Get Content -----------------------------------------------------
                
                soup_content = BeautifulSoup((requests.get('https://finance.yahoo.com/' + tag_a['href'])).text, 'html')

                for li_ in soup_content.find_all('p'):
                    text = li_.text
                    if text != '': st += li_.text + '\n'

                try :        

                    df['Date'],df['Title'],df['Description'],df['Img'],df['Link'],df['Source'],df['Content']  = datetime.datetime.strptime(soup_content.find('time')['datetime'], '%Y-%m-%dT%H:%M:%S.%f%z').strftime('%d/%m/%Y'),tag_a.text,l.find('p').text,url_img,'https://finance.yahoo.com/' + tag_a['href'],'yahoo',st
                    share_news = [i.text for i in soup_content.find_all('div', {'class': 'xray-card-row-title'})]
                    tag_share_news[df['Title']] = share_news
                    chest.append(df)
                except TypeError: pass
                    

    return chest,tag_share_news

def Kaohoon_news(triker):

    chest,I,tag_share_news  = [],0,{}
    #https://www.kaohoon.com/?s= , https://www.kaohoon.com/tag/{triker}
    url = requests.get(f"https://www.kaohoon.com/?s={triker}")
    soup = BeautifulSoup(url.text, 'html')
    for ultag in soup.find_all('ul', {'class': 'posts-items'}):

        for li in ultag.find_all('li'):

            df,st  = {},''
            text = (li.text).split('\n')

            df['Date'],df['Title'],df['Description'],df['Img'],df['Link'],df['Source'] = text[3],text[4],text[5],li.find('img')['src'],li.find('a')['href'],'kaohoon'

            soup = BeautifulSoup((requests.get(f"{df['Link']}")).text, 'html')

            div = soup.find('div', {'class': 'entry-content entry clearfix'})

            if str(div) == 'None' : return {}
            for li in div.find_all('p'):
                text = li.text
                if text != '':
                    st += li.text + '\n'
            
            df['Content'] = st
            tag_share_news[df['Title']] = triker

            if st != '': chest.append(df)
            
    return chest,tag_share_news

def get_id_News(title):
    # connect to the database
    conn = sqlite3.connect(r'C:\Users\JourneyQ\OneDrive - kmutnb.ac.th\Desktop\Quick_file\year_2-S_2\Project_sofedev_2\Manage_Share\Database_convert\share_V3.sqlite')
    c = conn.cursor()
    id = ''
    # search for words in the table
    c.execute(f"""SELECT * FROM News WHERE title="{title}" """)
    results = c.fetchall()

    if results != []: id = str(results[0][0])
        
    else : id = 'None'

    # close the database connection
    conn.close()

    return id

def translate_text(text):

    detector = Translator()

    dec_lan = ''
    for sec in range(int(len(text)/1000)+1):

        dec_lan += detector.translate(text[1000*sec:1000*(sec+1)],des='en').text

    return dec_lan


def Separate_words(text):

    w = text.split(r'\n')
    for content in w : text+= content + ' '

    nlp = spacy.load('en_core_web_sm')
    # nlp = en_core_web_sm.load()
    doc = nlp(text)

    word = []

    for token in doc.ents:
        
        if token.label_ != 'DATE' and token.label_ !='CARDINAL' and token.label_ !='TIME':
            # print(token.text,token.label_)     
            word += token.text.split('"')

    return list(numpy.unique(word))

def filter_special_2(words):
    # Define regular expression pattern to match words
    word_filter = []

    # Find all matches of the pattern in the text
    for word in words :
        s = 0
        for ch in word:

            if isinstance(ch , str) and ch.isnumeric(): s = 1

        if s == 0: word_filter.append(word)
                
    return list(numpy.unique(word_filter))

def search_share_in_table(words,NewsId,source):
    # connect to the database
    conn = sqlite3.connect(r'C:\Users\JourneyQ\OneDrive - kmutnb.ac.th\Desktop\Quick_file\year_2-S_2\Project_sofedev_2\Manage_Share\Database_convert\share_V3.sqlite')
    c = conn.cursor()
    share = []

    for word in words : 

        w = word
        if source == 'kaohoon': w = word + '.BK'

        # search for words in the table
        c.execute(f"""SELECT * FROM Information WHERE Symbol="{w}" or Sname="{word}"; """)
        results = c.fetchall()

        if results != []:
            data = {}
            data['SymbolId'],data['NewsId'] = results[0][0],NewsId
            share.append(data)

    # close the database connection
    conn.close()

    return share

def find_location(words,NewsId):

    geolocator = Nominatim(user_agent="Geolocation")
    loca,extra = [],[]
    for i in words :
  
        location = geolocator.geocode(f"{i}", exactly_one=True, namedetails=True, addressdetails=True,timeout=12000, language='en')

        if str(location) != 'None' :

            data = {}

            try :
                if i in ['Africa', 'Europe', 'Asia', 'North America', 'South America', 'Antarctica', 'Australia','South Pole','North pole'] :
                    data['Lname'],data['Country'],data['Latitude'],data['Longitude'],data['NewsId'] = i,'',location.latitude, location.longitude,NewsId
                else:
                    data['Lname'],data['Country'],data['Latitude'],data['Longitude'],data['NewsId'] = i,location.raw['address']['country'],location.latitude, location.longitude,NewsId

                loca.append(data)

            except KeyError: extra.append(i)
                
    return loca

def add_data_to_db(table_name, column ,data):

    conn = sqlite3.connect(r'C:\Users\JourneyQ\OneDrive - kmutnb.ac.th\Desktop\Quick_file\year_2-S_2\Project_sofedev_2\Manage_Share\Database_convert\share_V3.sqlite')
    c = conn.cursor()

    # Create a string with placeholders for each value in the data tuple
    placeholders = ",".join(["?" for _ in data])

    # Construct the SQL query string
    query_string = f"INSERT INTO {table_name} ({column}) VALUES ({placeholders})"

    # Execute the query and commit the changes
    c.execute(query_string, data)
    conn.commit()

    # Close the connection
    conn.close()

def save_into_db(table,dic):

    df = pd.DataFrame(dic)
    con = sqlite3.connect(r'C:\Users\JourneyQ\OneDrive - kmutnb.ac.th\Desktop\Quick_file\year_2-S_2\Project_sofedev_2\Manage_Share\Database_convert\share_V3.sqlite')
    cur = con.cursor()    
    newshare = df.to_sql(table,con,if_exists='append', index=False)
    con.commit()
    con.close

In [3]:
tickers = ['ACE.BK', 'ADVANC.BK', 'AEONTS.BK', 'AMATA.BK', 'AOT.BK', 'AP.BK', 'AWC.BK', 'BAM.BK',
       'BANPU.BK', 'BBL.BK', 'BCH.BK', 'BCP.BK', 'BCPG.BK', 'BDMS.BK', 'BEC.BK', 'BEM.BK',
       'BGRIM.BK', 'BH.BK', 'BLA.BK', 'BTS.BK', 'CBG.BK', 'CENTEL.BK', 'CHG.BK', 'CK.BK', 'CKP.BK',
       'COM7.BK', 'CPALL.BK', 'CPF.BK', 'CPN.BK', 'CRC.BK', 'DOHOME.BK', 'DTAC.BK', 'EA.BK',
       'EGCO.BK', 'EPG.BK', 'ESSO.BK', 'FORTH.BK', 'GLOBAL.BK', 'GPSC.BK', 'GULF.BK', 'GUNKUL.BK',
       'HANA.BK', 'HMPRO.BK', 'INTUCH.BK', 'IRPC.BK', 'IVL.BK', 'JMART.BK', 'JMT.BK', 'KBANK.BK',
       'KCE.BK', 'KEX.BK', 'KKP.BK', 'KTB.BK', 'KTC.BK', 'LH.BK', 'MAJOR.BK', 'MEGA.BK', 'MINT.BK',
       'MTC.BK', 'ONEE.BK', 'OR.BK', 'ORI.BK', 'OSP.BK', 'PLANB.BK', 'PSL.BK', 'PTG.BK', 'PTT.BK',
       'PTTEP.BK', 'PTTGC.BK', 'QH.BK', 'RATCH.BK', 'RBF.BK', 'RCL.BK', 'SAWAD.BK', 'SCB.BK',
       'SCC.BK', 'SCGP.BK', 'SINGER.BK', 'SPALI.BK', 'SPRC.BK', 'STA.BK', 'STARK.BK', 'STEC.BK',
       'STGT.BK', 'SUPER.BK', 'SYNEX.BK', 'TASCO.BK', 'TCAP.BK', 'THANI.BK', 'TIDLOR.BK',
       'TIPH.BK', 'TISCO.BK', 'TOP.BK', 'TQM.BK', 'TRUE.BK', 'TTA.BK', 'TTB.BK', 'TU.BK', 'VGI.BK',
       'WHA.BK']

In [31]:
all_news,tags = [],[]
for i in tickers[:10]:
    print(i)
    data,tag= Kaohoon_news(i.split('.BK')[0])
    all_news+=data
    tags.append(tag)
    print(data)
    print(tag)
    print('-------------------------------------------------------')

ACE.BK
[{'Date': '13/03/2023', 'Title': 'BCPG จับมือ Ampace รุกธุรกิจผลิต “แบตเตอรี่” รองรับดีมานด์ภาค “ครัวเรือน-อุตสาหกรรม”', 'Description': 'BCPG จับมือ Ampace บริษัทร่วมทุนของ ATL และ CATL จ่อสร้างธุรกิจผลิตแบตเตอรี่รองรับความต้องการใช้ไฟฟ้าภาคครัวเรือน อุตสาหกรรมขนาดกลาง และมอเตอร์ไซค์ไฟฟ้า', 'Img': 'https://www.kaohoon.com/wp-content/uploads/2023/03/BCPG_2023-03-13_BCPG-จับมือ-Ampace-บริษัทร่วมทุนของ-ATL-และ-CATL.jpg', 'Link': 'https://www.kaohoon.com/pr/594298', 'Source': 'kaohoon', 'Content': 'นายนิวัติ อดิเรก ประธานเจ้าหน้าที่บริหารและกรรมการผู้จัดการใหญ่ บริษัท บีซีพีจี จำกัด (มหาชน) หรือ BCPG\xa0และนายเจอรี่ เจีย ประธานเจ้าหน้าที่บริหาร บริษัท เซี่ยเหมิน เอมเพส เทคโนโลยี จำกัด (Xiamen Ampace Technology Limited) ได้ร่วมลงนามบันทึกความเข้าใจ (MOU) ในการพัฒนาธุรกิจแบตเตอรี่ เพื่ออุตสาหกรรมยานยนต์ไฟฟ้าสองล้อและสามล้อ แบตเตอรี่สำหรับติดตั้งในภาคครัวเรือน\xa0 (Residential) ในภาคอุตสาหกรรม (Commercial & Industrial) และโอกาสในการจัดตั้งโรงงานผลิตแบตเตอรี่ระดับโมดูลหรือแพ็ค รวมถึงระด

In [35]:
# news = pd.read_csv('New.csv')
# del news['Unnamed: 0']
# del news['Tag']
news = pd.DataFrame(all_news)
df = news

In [51]:
shareNews = []
locaNew = []
column = 'Date,Title,Description,Img,Link,Source,Content'
data = list(news.itertuples(index=False, name=None))
# len(data))
for i in range(1,len(data)):

    # ตรวจสอบ News ว่ามีใน database รึยัง
    NewsId = get_id_News(df['Title'][i])
    # print(NewsId)

    if NewsId == 'None':
        # ถ้าไม่มีจะเพิ่ม แต่ถ้ามีจะแสดงว่าเคยดึงสถานที่กับหุ้นไปแล้วจะหยุดการทำงาน
        add_data_to_db('News',column,data[i])
        
        # ดึง id ใหม่อีกครั้งจากหุ้นที่พึงเพิ่มเข้าไป
        NewsId = get_id_News(df['Title'][i])
        print(NewsId)

        #เริ่มการประมวลหาสถานที่และหุ้น
        text = df['Content'][i]
        print(text)
        en = translate_text(text)
        print("text is ",en)
        print('--------------------------------------')

        words = Separate_words(en)
        print("Words target is ",words)
        print('--------------------------------------')

        words = filter_special_2(words)
        print("Words filter is ",words)
        print('--------------------------------------')

        # words.append(df['Tag'][i])
        share,words = search_share_in_table(words,NewsId,df['Source'][i])
        print("Share in text is ",share)
        shareNews += share
        print("Words target is ",words)

        print('--------------------------------------')

        loca = find_location(words,NewsId)
        print("location in text is ",loca)
        locaNew += loca
        print(' ')
        print('--------------------------------------')

13
นายธนะชัย บัณฑิตวรภูมิ ประธานเจ้าหน้าที่บริหาร บริษัท แอ๊บโซลูท คลีน เอ็นเนอร์จี้ จำกัด (มหาชน) หรือ ACE ผู้นำด้านธุรกิจพลังงานสะอาดของไทย เปิดเผยผลการดำเนินงานปี 2565 ของ ACE ว่า สามารถทำรายได้จากการขายและบริการรวม 6,917.0 ล้านบาท เพิ่มขึ้น 21% จากปี 2564 ที่ทำได้ 5,726.9 ล้านบาท แม้ปี 2565 จะเป็นปีที่ไม่มีการเปิดดำเนินการเชิงพาณิชย์ (COD) ของโรงไฟฟ้าเพิ่มเติมจากปี 2564 ก็ตาม ด้านกำไรสุทธิปี 2565 สามารถทำได้ 1,282.0 ล้านบาท ลดลงจากปี 2564 ที่ทำได้ 1,505.7 ล้านบาท เนื่องจากในปี 2564 บริษัทฯ มีกำไรจากรายการพิเศษซึ่งส่วนใหญ่เกิดจากอัตราแลกเปลี่ยนที่มากกว่าปี 2565 รวมทั้งปี 2565 บริษัทฯ มีค่าใช้จ่ายในการบริหารที่เพิ่มขึ้นกว่าปี 2564 ซึ่งส่วนใหญ่เป็นค่าใช้จ่ายที่เกิดขึ้นเพื่อรองรับการขยายกิจการ เช่น ค่าใช้จ่ายเกี่ยวกับพนักงานตามจำนวนพนักงานที่เพิ่มขึ้น ค่าใช้จ่ายที่เกี่ยวกับการประมูลโครงการต่างๆ และการเริ่มต้นโครงการใหม่ เป็นต้น
“สำหรับทิศทางธุรกิจ ACE ปี 2566 ยังคงให้ความสำคัญกับการเพิ่มประสิทธิภาพ การขยายธุรกิจ และการมองหาโอกาสทางธุรกิจใหม่ๆ ในด้านพลังงานสะอาดทุกประเภทอย่างต่อเนื่อง ท

In [53]:
locainNews = pd.DataFrame(locaNew)
shareinNews = pd.DataFrame(shareNews)

In [54]:
# save_into_db('Location_in_News',locainNews)
# save_into_db('Share_in_News',shareinNews)

In [160]:
shareNews = []
locaNew = []
column = 'Date,Title,Description,Img,Link,Source,Content'
data = list(news.itertuples(index=False, name=None))
# len(data))
i = 322
NewsId = get_id_News(df['Title'][i])
print(NewsId)
if NewsId == '328':
    # ถ้าไม่มีจะเพิ่ม แต่ถ้ามีจะแสดงว่าเคยดึงสถานที่กับหุ้นไปแล้วจะหยุดการทำงาน
    # add_data_to_db('News',column,data[i][:-1])
        
    # ดึง id ใหม่อีกครั้งจากหุ้นที่พึงเพิ่มเข้าไป
    NewsId = get_id_News(df['Title'][i])
    print(NewsId)

    #เริ่มการประมวลหาสถานที่และหุ้น
    text = df['Content'][i]
    print(text)
    en = translate_text(text)
    print("text is ",en)
    print('--------------------------------------')

    words = Separate_words(en)
    print("Words target is ",words)
    print('--------------------------------------')
    words = filter_special_2(words)
    print("Words filter is ",words)
    print('--------------------------------------')

    # words.append(df['Tag'][i])
    share,words = search_share_in_table(words,NewsId,df['Source'][i])
    print("Share in text is ",share)
    shareNews += share
    print("Words target is ",words)

    print('--------------------------------------')

    loca = find_location(words,NewsId)
    print("location in text is ",loca)
    locaNew += loca
    print(' ')
    print('--------------------------------------')

328
328
นายฉัตรพล ศรีประทุม ผู้อำนวยการ ฝ่ายพัฒนากลยุทธ์และวางแผนการลงทุน บริษัท พลังงานบริสุทธิ์ จำกัด (มหาชน) หรือ EA เปิดเผยว่า โครงการแลกเปลี่ยนคาร์บอนเครดิตภายใต้ความตกลงปารีส Article 6 ของรถโดยสารประจำทาง EV นี้ เป็นโครงการอันดับแรกๆ ของโลก  และเป็นโครงการแรกของทวีปเอเชียโดยทาง EA มีความมุ่งมั่นที่จะเป็นผู้นำในการส่งเสริมความร่วมมือกันระหว่างประเทศในด้านการรักษาสิ่งแวดล้อม การเดินหน้าของโครงการเราจะเป็นการสนับสนุนให้เราก้าวเข้าสู่สังคมเศรษฐกิจแบบปลอดคาร์บอน และช่วยกระตุ้นบรรยากาศที่ดีสำหรับภาคเอกชนในการพัฒนากิจกรรมที่ช่วยรักษา รวมถึงปกป้องสิ่งแวดล้อม
ด้าน Mr. Michael Brennwald, Head International, Klik Foundation กล่าวว่า โครงการแลกเปลี่ยนคาร์บอนเครดิตภายใต้ความตกลงปารีส Article 6 ของรถโดยสารประจำทาง EV นี้ เป็นโครงการนำร่องเพื่อการสนับสนุนกิจกรรมการรักษาสิ่งแวดล้อมแบบยั่งยืน การแลกเปลี่ยนคาร์บอนเครดิตผ่าน Article 6 นั้นมีการร่วมกันพัฒนามาอย่างแข็งขันจากทุกภาคส่วน
นอกจากนี้ยังมองหาโอกาสในการร่วมมือกับภาคเอกชนในประเทศไทยและประเทศข้างเคียงเพื่อที่จะสร้างโครงการในการร่วมมือกันระหว่า

-------------------------------------------- Yahoo --------------------------------------------

In [4]:
html = Set_up_WebScraping('https://finance.yahoo.com/topic/stock-market-news/')

C:\Users\JourneyQ\AppData\Local\Temp\ipykernel_23368\3223181278.py:3: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(r"C:\Users\JourneyQ\OneDrive - kmutnb.ac.th\Desktop\Quick_file\year_2-S_2\Project_sofedev_2\Schap\chromedriver.exe")


In [97]:
import sqlite3
import pandas as pd
sql = """ SELECT Inf.Symbol
FROM Information as Inf
Inner join Stock_price_day as s on s.SymbolId = Inf.SymbolId
where Inf.MarketId = 2
Group By Inf.SymbolId

"""
con = sqlite3.connect(r'C:\Users\JourneyQ\OneDrive - kmutnb.ac.th\Desktop\Quick_file\year_2-S_2\Project_sofedev_2\Manage_Share\Database_convert\share_V3.sqlite')
cur = con.cursor()    
cur.execute(sql)
results = cur.fetchall()
df = pd.read_sql(sql, con)
con.commit()
con.close

<function Connection.close()>

In [98]:
len(results)

38

In [99]:
nasdaq = []
for i in results:

    nasdaq.append(i[0])

In [100]:
nasdaq

['AAPL',
 'ADBE',
 'ADI',
 'ADP',
 'AMAT',
 'AMD',
 'AMGN',
 'AMZN',
 'ASML',
 'AVGO',
 'AZN',
 'BKNG',
 'CMCSA',
 'COST',
 'CSCO',
 'GILD',
 'GOOG',
 'GOOGL',
 'HON',
 'INTC',
 'INTU',
 'ISRG',
 'JD',
 'MDLZ',
 'META',
 'MSFT',
 'NFLX',
 'NVDA',
 'PCAR',
 'PDD',
 'PEP',
 'PYPL',
 'QCOM',
 'SBUX',
 'SNY',
 'TMUS',
 'TSLA',
 'TXN']

In [81]:
nasdaq = list(numpy.unique(nasdaq))

In [101]:
print(nasdaq)

['AAPL', 'ADBE', 'ADI', 'ADP', 'AMAT', 'AMD', 'AMGN', 'AMZN', 'ASML', 'AVGO', 'AZN', 'BKNG', 'CMCSA', 'COST', 'CSCO', 'GILD', 'GOOG', 'GOOGL', 'HON', 'INTC', 'INTU', 'ISRG', 'JD', 'MDLZ', 'META', 'MSFT', 'NFLX', 'NVDA', 'PCAR', 'PDD', 'PEP', 'PYPL', 'QCOM', 'SBUX', 'SNY', 'TMUS', 'TSLA', 'TXN']


In [102]:
all_news,tags = [],{}
for i in nasdaq[:100]:
    print(i)
    data,tag= YahooUpdateNews(i)
    all_news+=data
    tags.update(tag)
    print(data)
    print(tag)
    print('-------------------------------------------------------')

AAPL
['GOOGL', 'VRTX', 'AMZN', 'INTC', 'AAPL']
['BRK-A', 'AAPL', 'OXY']
['AAPL']
['MSFT', 'T-PC', 'CRWD', 'AAPL']
['AAPL', 'AMZN']
['BRK-A', 'AAPL', 'AMZN', 'SNOW', 'AXP']
['AAPL', 'JNJ', 'MSFT', 'CVX', 'JPM', 'XOM', 'VZ']
['AAPL']
['AAPL']
['WMT', 'AMZN', 'UNH', 'AAPL', 'XOM', 'SNPMF', 'VWAPY']
[{'Date': '13/03/2023', 'Title': 'Prediction: These 3 Stocks Will Be in the Dow by 2030', 'Description': 'Being added to the Dow Jones Industrial Average would just be another feather in the cap for these successful stocks.', 'Img': 'https://s.yimg.com/uu/api/res/1.2/LNOndugyea8ZUYcInz_xgQ--~B/Zmk9c3RyaW07aD0xMjM7cT04MDt3PTIyMDthcHBpZD15dGFjaHlvbg--/https://media.zenfs.com/en/motleyfool.com/a76e92fd9ab3d0f839b73a127ff33802', 'Link': 'https://finance.yahoo.com//m/617dba01-475e-3991-a026-54d3a5d5e03f/prediction-these-3-stocks.html', 'Source': 'yahoo', 'Content': 'Being added to the Dow Jones Industrial Average would just be another feather in the cap for these successful stocks.\n'}, {'Date': '13

In [103]:
df = pd.DataFrame(all_news)

In [114]:
shareNews = []
locaNew = []
column = 'Date,Title,Description,Img,Link,Source,Content'
data = list(df.itertuples(index=False, name=None))
# len(data)) 0,100
for i in range(100,len(data)):

    # ตรวจสอบ News ว่ามีใน database รึยัง
    NewsId = get_id_News(df['Title'][i])
    # print(NewsId)
    print(NewsId)

    if NewsId == 'None':
        # # ถ้าไม่มีจะเพิ่ม แต่ถ้ามีจะแสดงว่าเคยดึงสถานที่กับหุ้นไปแล้วจะหยุดการทำงาน
        add_data_to_db('News',column,data[i])

        # # ดึง id ใหม่อีกครั้งจากหุ้นที่พึงเพิ่มเข้าไป
        NewsId = get_id_News(df['Title'][i])
        print(NewsId)

        # # #เริ่มการประมวลหาสถานที่และหุ้น
        text = df['Content'][i]
        print(text)
        en = translate_text(text)
        print("text is ",en)
        print('--------------------------------------')

        words = Separate_words(en)
        print("Words target is ",words)
        print('--------------------------------------')
        words += tags[df['Title'][i]]
        words = filter_special_2(words)
        print("Words filter is ",words)
        print('--------------------------------------')

        share,words = search_share_in_table(words,NewsId,df['Source'][i])
        print("Share in text is ",share)
        shareNews += share
        print("Words target is ",words)

        print('--------------------------------------')

        loca = find_location(words,NewsId)
        print("location in text is ",loca)
        locaNew += loca
        print(' ')
        print('--------------------------------------')

None
214
Booking Holdings (BKNG) could be a solid addition to your portfolio given its recent upgrade to a Zacks Rank #2 (Buy). An upward trend in earnings estimates -- one of the most powerful forces impacting stock prices -- has triggered this rating change.
The Zacks rating relies solely on a company's changing earnings picture. It tracks EPS estimates for the current and following years from the sell-side analysts covering the stock through a consensus measure -- the Zacks Consensus Estimate.
Since a changing earnings picture is a powerful factor influencing near-term stock price movements, the Zacks rating system is very useful for individual investors. They may find it difficult to make decisions based on rating upgrades by Wall Street analysts, as these are mostly driven by subjective factors that are hard to see and measure in real time.
As such, the Zacks rating upgrade for Booking Holdings is essentially a positive comment on its earnings outlook that could have a favorable i

In [115]:
locainNews = pd.DataFrame(locaNew)
shareinNews = pd.DataFrame(shareNews)

In [116]:
save_into_db('Location_in_News',locainNews)
save_into_db('Share_in_News',shareinNews)